In [ ]:
# ./elasticsearch-7.12.1/bin/elasticsearch -d


In [1]:
!nvidia-smi

/bin/bash: nvidia-smi: command not found


In [2]:
import sys
import os

#!{sys.executable} -m pip install elasticsearch

import matplotlib.pyplot as plt
import io
import unicodedata
import numpy as np
import re
import string
import csv                 
import pickle
import json
import json_lines
import pandas as pd
import math

from six import string_types
from typing import Dict
from pathlib import Path
from functools import partial
from collections import OrderedDict
from argparse import ArgumentParser

import tqdm

import haystack
import elasticsearch

#from haystack.preprocessor.cleaning import clean_wiki_text
#from haystack.preprocessor.utils import convert_files_to_dicts, fetch_archive_from_http
#from haystack.reader.farm import FARMReader
#from haystack.reader.transformers import TransformersReader
#from haystack.utils import print_answers
from haystack.document_store.elasticsearch import ElasticsearchDocumentStore
from haystack.retriever.sparse import ElasticsearchRetriever

import lineflow as lf
from transformers import AlbertForMultipleChoice, AlbertTokenizer, AdamW, AlbertConfig, AlbertModel
import pytorch_lightning as pl
from pytorch_lightning.metrics import functional as FM

import torch
from torch.utils.data import DataLoader, SequentialSampler, RandomSampler

import time

from pytorch_lightning import seed_everything
import random

seed_everything(42, workers=True)
random.seed(42)
np.random.seed(42)

KeyboardInterrupt: 

In [ ]:
!curl localhost:9200

In [ ]:
document_store = ElasticsearchDocumentStore(host="localhost", username="", password="", index="document")

In [ ]:
document_store.get_document_count()

In [ ]:
retriever = ElasticsearchRetriever(document_store=document_store)

In [ ]:
# print(retriever.retrieve(query="What colour is the sun? Yellow", top_k=10))

In [8]:
_article = ""
for result in retriever.retrieve(query="What colour is the sun? Yellow", top_k=3):
    print(result.text)
    #    _article = _article + result["text"] + ". "

06/16/2021 10:25:58 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:15.278s]


For example, when the sun is higher in the sky, pillars are white or bright yellow in colour.

the cora sun drop diamond is the largest known yellow pear shaped diamond weighing it was sold for million at sotheby auction in geneva and set world record price for yellow diamond history the sun drop has very short history it was found in south africa in within kimberlite pipe tests show that the diamond was formed from to billion years ago after that on february it was kept in the vault of the london natural history museum together with many other precious stones such as the duke of devonshire emerald and the aurora pyramid of hope where it stayed for six months in november it was sold at an auction in geneva for just over million the stone was cut and owned by the diamond manufacturing company cora international based in new york city it was sold at the auction by sotheby the sun drop was bought by telephone bidder who decided to remain anonymous including commission and taxes the buyer 

In [ ]:
MAX_LEN = 512
NUM_LABELS = 4
label_map = {"A": 0, "B": 1, "C": 2, "D": 3}
BATCH_SIZE = 8
iter_version = "4"

In [9]:
t_dataset = []

def raw_samples_to_dataset(samples, daset):
    datas = []
    i = 0
    for sample in samples:
        i+=1
        if i%250 == 0:
            print(i)

        _id = sample["id"]
        _uniques = []
        _rscore = []
        _article = []
        _options = []
        toomany = 0
            
        _answer = sample["answerKey"]
        
        if _answer == "5" or _answer == "E":
            toomany = random.randint(1, 4)   
            _answer = str(toomany)
            print(_id)
            print("Too many :")
            print(toomany)            
            
        if _answer == "1":
            _answer = "A"
        if _answer == "2":
            _answer = "B"
        if _answer == "3":
            _answer = "C"
        if _answer == "4":
            _answer = "D"        
        if _answer not in ["A", "B", "C", "D"]:
            print(_id)
            print("skipped")
            continue
        assert(_answer in ["A", "B", "C", "D"])

        _question = sample["question"]['stem']   
        for idx in range(len(sample['question']['choices'])): 
            answer = sample["question"]['choices'][idx]['label']
            if answer == "1":
                answer = "A"
            if answer == "2":
                answer = "B"
            if answer == "3":
                answer = "C"
            if answer == "4":
                answer = "D"
            
            if answer not in ["A", "B", "C", "D"]:
                continue
                
            if toomany > 0 and _answer == answer:
                _options.append(sample["question"]['choices'][4]['text'])
                continue                       
            
            _options.append(sample["question"]['choices'][idx]['text'])

        if len(_options) < 4:
            print(_id)
            print("skipped, less than 4 options")
            continue
        assert(len(_options) == 4)            

        for idx in range(len(_options)): 
            _facts = ""
            _scores = []
            for result in retriever.retrieve(query= _question + " " + _options[idx], top_k=4):
                _facts = _facts + " " + result.text
                _scores.append(result.score)
            _rscore.append(_scores)
            _article.append(_facts)
                
#        print(_article)

        data = {
#                "str_id": _id,
                "id": _id,
                "article": _article,
                "options": _options,
                "question": _question,
                "answer": _answer,
                "optionscore": [],
                "rscore": _rscore
                }
        datas.append(data)
        daset.append(data)
    return lf.Dataset(datas)   

In [10]:
def preprocess(tokenizer: AlbertTokenizer, x: Dict) -> Dict:

    choices_features = []
    i=0
    option: str
    for option in x["options"]:
        text_a = x["article"][i]
        i+=1
        text_b = x["question"] + " " + option

        inputs = tokenizer.encode_plus(
                text_a,
                text_b,
                add_special_tokens=True,
                max_length=MAX_LEN
                )
        input_ids, token_type_ids = inputs["input_ids"], inputs["token_type_ids"]
        attention_mask = [1] * len(input_ids)

        pad_token_id = tokenizer.pad_token_id
        padding_length = MAX_LEN - len(input_ids)
        input_ids = input_ids + ([pad_token_id] * padding_length)
        attention_mask = attention_mask + ([0] * padding_length)
        token_type_ids = token_type_ids + ([pad_token_id] * padding_length)

        assert len(input_ids) == MAX_LEN, "Error with input length {} vs {}".format(len(input_ids), MAX_LEN)
        assert len(attention_mask) == MAX_LEN, "Error with input length {} vs {}".format(len(attention_mask), MAX_LEN)
        assert len(token_type_ids) == MAX_LEN, "Error with input length {} vs {}".format(len(token_type_ids), MAX_LEN)

        choices_features.append({
            "input_ids": input_ids,
            "attention_mask": attention_mask,
            "token_type_ids": token_type_ids,
            })

    labels = label_map.get(x["answer"], -1)
    label = torch.tensor(labels).long()

    return {
            "id": x["id"],
            "label": label,
            "input_ids": torch.tensor([cf["input_ids"] for cf in choices_features]),
            "attention_mask": torch.tensor([cf["attention_mask"] for cf in choices_features]),
            "token_type_ids": torch.tensor([cf["token_type_ids"] for cf in choices_features]),
            }

In [11]:
#--------------------------------------------------------------------
#-------------------------Dataloader functions-----------------------
#--------------------------------------------------------------------



#--------------------------------------------------------------------
#-------------------------ARC Easy-----------------------------------
#--------------------------------------------------------------------

def get_arc_easy_test_dataloader(tokenizer, datadir: str = './ARC-V1-Feb2018-2/ARC-Easy', cachedir: str = "./"):
    datadir = Path(datadir)
    datafile = "ARC-Easy-Test.jsonl"
    cachedir = Path(cachedir)
    filename = "_e_test_arc"
    cachefile = "cache" + iter_version + filename + ".cache"
    ds_file = "DS" + iter_version + filename + ".pkl"
    dl_file = "DL" + iter_version + filename + ".pkl"
    
    if os.path.isfile(cachedir / cachefile):
        os.remove(cachedir / cachefile)
    if os.path.isfile(ds_file):
        os.remove(ds_file)
    if os.path.isfile(dl_file):
        os.remove(dl_file)
        
        
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    with open(datadir / datafile) as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    pickle.dump(test, open(ds_file, "wb"))   
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / cachefile),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )
    
    pickle.dump(test_dataloader, open(dl_file, "wb"))
    return test_dataloader

def get_arc_easy_train_dataloader(tokenizer, datadir: str = './ARC-V1-Feb2018-2/ARC-Easy', cachedir: str = "./"):
    datadir = Path(datadir)
    datafile = "ARC-Easy-Train.jsonl"
    cachedir = Path(cachedir)
    filename = "_e_train_arc"
    cachefile = "cache" + iter_version + filename + ".cache"
    ds_file = "DS" + iter_version + filename + ".pkl"
    dl_file = "DL" + iter_version + filename + ".pkl"
    
    if os.path.isfile(cachedir / cachefile):
        os.remove(cachedir / cachefile)
    if os.path.isfile(ds_file):
        os.remove(ds_file)
    if os.path.isfile(dl_file):
        os.remove(dl_file)
        
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    with open(datadir / datafile) as f:
        for item in json_lines.reader(f):
            test_samples.append(item)    
    
    in_samples = [[] for i in range(math.ceil(len(test_samples)/500)+1)]    
    i = 0
    for item in test_samples:
        i = i+1
        in_samples[math.floor(i/500)].append(item)
    j=0
    test_res = []
    while j <= math.floor(i/500):
        backupfile = "ds_backup_"+str(j)+ ".pkl"
        if os.path.isfile(backupfile):
            j = j+1
            print("loading")
            print(backupfile)
            with open(backupfile,"rb") as f:
                appen = pickle.load(f)
                test_res.append(appen)
            continue
        test = raw_samples_to_dataset(in_samples[j],t_dataset)        
        pickle.dump(test, open(backupfile, "wb"))  
        test_res.append(test)
        j = j+1
    
    j=0
    test = test_res[0]
    while j < math.floor(i/500): 
        j = j+1
        test = test + test_res[j]
        
    pickle.dump(test, open(ds_file, "wb"))   
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / cachefile),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )
    
    pickle.dump(test_dataloader, open(dl_file, "wb"))
    return test_dataloader


def get_arc_easy_dev_dataloader(tokenizer, datadir: str = './ARC-V1-Feb2018-2/ARC-Easy', cachedir: str = "./"):
    datadir = Path(datadir)
    datafile = "ARC-Easy-Dev.jsonl"
    cachedir = Path(cachedir)
    filename = "_e_dev_arc"
    cachefile = "cache" + iter_version + filename + ".cache"
    ds_file = "DS" + iter_version + filename + ".pkl"
    dl_file = "DL" + iter_version + filename + ".pkl"
    
    if os.path.isfile(cachedir / cachefile):
        os.remove(cachedir / cachefile)
    if os.path.isfile(ds_file):
        os.remove(ds_file)
    if os.path.isfile(dl_file):
        os.remove(dl_file)
        
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    with open(datadir / datafile) as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    pickle.dump(test, open(ds_file, "wb"))   
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / cachefile),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )
    
    pickle.dump(test_dataloader, open(dl_file, "wb"))
    return test_dataloader






#-------------------------------------------------------------------------
#-------------------------ARC Challenge-----------------------------------
#-------------------------------------------------------------------------

def get_arc_challenge_test_dataloader(tokenizer, datadir: str = './ARC-V1-Feb2018-2/ARC-Challenge', cachedir: str = "./"):
    datadir = Path(datadir)
    datafile = "ARC-Challenge-Test.jsonl"
    cachedir = Path(cachedir)
    filename = "_c_test_arc"
    cachefile = "cache" + iter_version + filename + ".cache"
    ds_file = "DS" + iter_version + filename + ".pkl"
    dl_file = "DL" + iter_version + filename + ".pkl"
    
    if os.path.isfile(cachedir / cachefile):
        os.remove(cachedir / cachefile)
    if os.path.isfile(ds_file):
        os.remove(ds_file)
    if os.path.isfile(dl_file):
        os.remove(dl_file)
        
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    with open(datadir / datafile) as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    pickle.dump(test, open(ds_file, "wb"))   
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / cachefile),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )
    
    pickle.dump(test_dataloader, open(dl_file, "wb"))
    return test_dataloader

def get_arc_challenge_train_dataloader(tokenizer, datadir: str = './ARC-V1-Feb2018-2/ARC-Challenge', cachedir: str = "./"):
    datadir = Path(datadir)
    datafile = "ARC-Challenge-Train.jsonl"
    cachedir = Path(cachedir)
    filename = "_c_train_arc"
    cachefile = "cache" + iter_version + filename + ".cache"
    ds_file = "DS" + iter_version + filename + ".pkl"
    dl_file = "DL" + iter_version + filename + ".pkl"
    
    if os.path.isfile(cachedir / cachefile):
        os.remove(cachedir / cachefile)
    if os.path.isfile(ds_file):
        os.remove(ds_file)
    if os.path.isfile(dl_file):
        os.remove(dl_file)
        
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    with open(datadir / datafile) as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    pickle.dump(test, open(ds_file, "wb"))   
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / cachefile),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )
    
    pickle.dump(test_dataloader, open(dl_file, "wb"))
    return test_dataloader


def get_arc_challenge_dev_dataloader(tokenizer, datadir: str = './ARC-V1-Feb2018-2/ARC-Challenge', cachedir: str = "./"):
    datadir = Path(datadir)
    datafile = "ARC-Challenge-Dev.jsonl"
    cachedir = Path(cachedir)
    filename = "_c_dev_arc"
    cachefile = "cache" + iter_version + filename + ".cache"
    ds_file = "DS" + iter_version + filename + ".pkl"
    dl_file = "DL" + iter_version + filename + ".pkl"
    
    if os.path.isfile(cachedir / cachefile):
        os.remove(cachedir / cachefile)
    if os.path.isfile(ds_file):
        os.remove(ds_file)
    if os.path.isfile(dl_file):
        os.remove(dl_file)
        
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    with open(datadir / datafile) as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    pickle.dump(test, open(ds_file, "wb"))   
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / cachefile),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )
    
    pickle.dump(test_dataloader, open(dl_file, "wb"))
    return test_dataloader







#-------------------------------------------------------------------------
#-------------------------Openbook----------------------------------------
#-------------------------------------------------------------------------

def get_ob_test_dataloader(tokenizer, datadir: str = './OpenBookQA-V1-Sep2018/Data/Additional', cachedir: str = "./"):
    datadir = Path(datadir)
    datafile = "test_complete.jsonl"
    cachedir = Path(cachedir)
    filename = "_test_ob"
    cachefile = "cache" + iter_version + filename + ".cache"
    ds_file = "DS" + iter_version + filename + ".pkl"
    dl_file = "DL" + iter_version + filename + ".pkl"
    
    if os.path.isfile(cachedir / cachefile):
        os.remove(cachedir / cachefile)
    if os.path.isfile(ds_file):
        os.remove(ds_file)
    if os.path.isfile(dl_file):
        os.remove(dl_file)
        
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    with open(datadir / datafile) as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
                
    in_samples = [[] for i in range(math.ceil(len(test_samples)/500)+1)]    
    i = 0
    for item in test_samples:
        i = i+1
        in_samples[math.floor(i/500)].append(item)
    j=0
    test_res = []
    while j <= math.floor(i/500):
        backupfile = "ds_backup_"+str(j)+ ".pkl"
        if os.path.isfile(backupfile):
            j = j+1
            with open(backupfile) as f:
                test_res.append(pickle.load(f))    
            continue
        test = raw_samples_to_dataset(in_samples[j],t_dataset)        
        pickle.dump(test, open(backupfile, "wb"))  
        test_res.append(test)
        j = j+1
    
    j=0
    test = test_res[0]
    while j < math.floor(i/500): 
        j = j+1
        test = test + test_res[j]
        
    pickle.dump(test, open(ds_file, "wb")) 
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / cachefile),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )
    
    pickle.dump(test_dataloader, open(dl_file, "wb"))
    return test_dataloader



def get_ob_train_dataloader(tokenizer, datadir: str = './OpenBookQA-V1-Sep2018/Data/Additional', cachedir: str = "./"):
    datadir = Path(datadir)
    datafile = "train_complete.jsonl"
    cachedir = Path(cachedir)
    filename = "_train_ob"
    cachefile = "cache" + iter_version + filename + ".cache"
    ds_file = "DS" + iter_version + filename + ".pkl"
    dl_file = "DL" + iter_version + filename + ".pkl"
    
    if os.path.isfile(cachedir / cachefile):
        os.remove(cachedir / cachefile)
    if os.path.isfile(ds_file):
        os.remove(ds_file)
    if os.path.isfile(dl_file):
        os.remove(dl_file)
        
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    with open(datadir / datafile) as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    pickle.dump(test, open(ds_file, "wb"))   
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / cachefile),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )
    
    pickle.dump(test_dataloader, open(dl_file, "wb"))
    return test_dataloader



def get_ob_dev_dataloader(tokenizer, datadir: str = './OpenBookQA-V1-Sep2018/Data/Additional', cachedir: str = "./"):
    datadir = Path(datadir)
    datafile = "dev_complete.jsonl"
    cachedir = Path(cachedir)
    filename = "_dev_ob"
    cachefile = "cache" + iter_version + filename + ".cache"
    ds_file = "DS" + iter_version + filename + ".pkl"
    dl_file = "DL" + iter_version + filename + ".pkl"
    
    if os.path.isfile(cachedir / cachefile):
        os.remove(cachedir / cachefile)
    if os.path.isfile(ds_file):
        os.remove(ds_file)
    if os.path.isfile(dl_file):
        os.remove(dl_file)
        
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    with open(datadir / datafile) as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    pickle.dump(test, open(ds_file, "wb"))   
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / cachefile),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )
    
    pickle.dump(test_dataloader, open(dl_file, "wb"))
    return test_dataloader






#-------------------------------------------------------------------------
#-------------------------Commonsense-------------------------------------
#-------------------------------------------------------------------------

def get_commonqa_test_dataloader(tokenizer, datadir: str = './Commonsense', cachedir: str = "./"):
    datadir = Path(datadir)
    datafile = "test_rand_split_no_answers.jsonl"
    cachedir = Path(cachedir)
    filename = "_test_commonqa"
    cachefile = "cache" + iter_version + filename + ".cache"
    ds_file = "DS" + iter_version + filename + ".pkl"
    dl_file = "DL" + iter_version + filename + ".pkl"
    
    if os.path.isfile(cachedir / cachefile):
        os.remove(cachedir / cachefile)
    if os.path.isfile(ds_file):
        os.remove(ds_file)
    if os.path.isfile(dl_file):
        os.remove(dl_file)
        
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    with open(datadir / datafile) as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    pickle.dump(test, open(ds_file, "wb"))   
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / cachefile),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )
    
    pickle.dump(test_dataloader, open(dl_file, "wb"))
    return test_dataloader



def get_commonqa_train_dataloader(tokenizer, datadir: str = './Commonsense', cachedir: str = "./"):
    datadir = Path(datadir)
    datafile = "train_rand_split.jsonl"
    cachedir = Path(cachedir)
    filename = "_train_commonqa"
    cachefile = "cache" + iter_version + filename + ".cache"
    ds_file = "DS" + iter_version + filename + ".pkl"
    dl_file = "DL" + iter_version + filename + ".pkl"
    
    if os.path.isfile(cachedir / cachefile):
        os.remove(cachedir / cachefile)
    if os.path.isfile(ds_file):
        os.remove(ds_file)
    if os.path.isfile(dl_file):
        os.remove(dl_file)
        
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    with open(datadir / datafile) as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    
    in_samples = [[] for i in range(math.ceil(len(test_samples)/500)+1)]    
    i = 0
    for item in test_samples:
        i = i+1
        in_samples[math.floor(i/500)].append(item)
    j=0
    test_res = []
    while j <= math.floor(i/500):
        backupfile = "ds_backup_"+str(j)+ ".pkl"
        if os.path.isfile(backupfile):
            j = j+1
            print("loading")
            print(backupfile)
            with open(backupfile,"rb") as f:
                appen = pickle.load(f)
                test_res.append(appen)
            continue
        test = raw_samples_to_dataset(in_samples[j],t_dataset)        
        pickle.dump(test, open(backupfile, "wb"))  
        test_res.append(test)
        j = j+1
    
    j=0
    test = test_res[0]
    while j < math.floor(i/500): 
        j = j+1
        test = test + test_res[j]
  
    pickle.dump(test, open(ds_file, "wb"))   
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / cachefile),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )
    
    pickle.dump(test_dataloader, open(dl_file, "wb"))
    return test_dataloader



def get_commonqa_dev_dataloader(tokenizer, datadir: str = './Commonsense', cachedir: str = "./"):
    datadir = Path(datadir)
    datafile = "dev_rand_split.jsonl"
    cachedir = Path(cachedir)
    filename = "_dev_commonqa"
    cachefile = "cache" + iter_version + filename + ".cache"
    ds_file = "DS" + iter_version + filename + ".pkl"
    dl_file = "DL" + iter_version + filename + ".pkl"
    
    if os.path.isfile(cachedir / cachefile):
        os.remove(cachedir / cachefile)
    if os.path.isfile(ds_file):
        os.remove(ds_file)
    if os.path.isfile(dl_file):
        os.remove(dl_file)
        
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    with open(datadir / datafile) as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    pickle.dump(test, open(ds_file, "wb"))   
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / cachefile),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )
    
    pickle.dump(test_dataloader, open(dl_file, "wb"))
    return test_dataloader

In [12]:
class TestModel(pl.LightningModule):

    def __init__(self, model, test_dataloader, model2):
        super(TestModel, self).__init__()

        self.model = model
        self.model2 = model2
        self._test_dataloader = test_dataloader

    def test_step(self, batch, batch_idx):
        ids = batch["id"]
        labels = batch["label"]
        input_ids = batch["input_ids"]
        attention_mask = batch["attention_mask"]
        token_type_ids = batch["token_type_ids"]

        outputs = self.model(
                input_ids,
                token_type_ids=token_type_ids,
                attention_mask=attention_mask,
                labels=labels
        )
        outputs_pooler = self.model2(input_ids = torch.reshape(input_ids,(-1,512)),
                           token_type_ids=torch.reshape(token_type_ids,(-1,512)),
                           attention_mask=torch.reshape(attention_mask,(-1,512)))
        
        labels_hat = torch.argmax(outputs.logits, dim=1)
#        print(labels_hat)
#        print(labels)
#        print(batch["label"])
#        print(ids)
#        print(outputs.logits)
        i = 0
        j = int(len(batch["id"])/torch.cuda.device_count())
#        j = int(BATCH_SIZE/torch.cuda.device_count())
#        print(input_ids.size())
#        print(outputs_pooler.pooler_output.size()) 

        for element in outputs.logits:
#            print(element)
#            print(torch.cuda.current_device()*j+i)
#            print("---------------")
#            print(ids[torch.cuda.current_device()*j+i])
            for element2 in t_dataset:
                if element2["id"] == batch["id"][torch.cuda.current_device()*j+i]:
#                    print("!!!!!!!!!!!!!") 
#                    print("!!!!!!!!!!!!!") 
#                    print("!!!!!!!!!!!!!") 
                    hidden_pos = i*4
#                    hidden_pos = (torch.cuda.current_device()*j+i)*4
#                    print(hidden_pos) 
#                    print(outputs_pooler.pooler_output[hidden_pos:hidden_pos+4].cpu().numpy()) 
                    element2["optionscore"] = outputs_pooler.pooler_output[hidden_pos:hidden_pos+4].cpu().numpy()
#                    element2["optionscore"] = element.cpu().numpy()
#                    print(element2["optionscore"])
            i+=1
#        print(labels)
#        time.sleep(0.1)
        acc = FM.accuracy(labels_hat, labels)
#        print(acc)
        self.log('test_acc', acc, on_step=True, on_epoch=True, prog_bar=True, logger=True)

    def test_dataloader(self):
        return self._test_dataloader

In [13]:
def Generate_NN_file(src ,nn_file, runs):
    if os.path.isfile(nn_file):
        os.remove(nn_file)
    checkpoint_path = src
    checkpoint = torch.load(checkpoint_path)
    new_checkpoint = {}

    for key in checkpoint['state_dict'].keys():
        if 'model' in key:
            new_key = key[6:]
            new_checkpoint[new_key] = checkpoint['state_dict'][key]
        else:
            new_checkpoint[key] = checkpoint['state_dict'][key]

    config = AlbertConfig.from_pretrained('albert-base-v2')
    m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=new_checkpoint)
    m2 = AlbertModel.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=new_checkpoint)

    trainer_for_test = pl.Trainer(gpus=-1, accelerator='dp')
    model_for_test = TestModel(m, test_dataloader, m2)
    
    
    i = 0
    ret_saved = 0.0
    ret_data = t_dataset
    avg=0
    while i < runs: 
        ret = trainer_for_test.test(model=model_for_test)
        avg = avg + ret[0]["test_acc_epoch"]
        if ret[0]["test_acc_epoch"] > ret_saved:
            ret_saved = ret[0]["test_acc_epoch"]
            ret_data = t_dataset
        i = i+1
    avg = avg/i    
    pickle.dump(ret_data, open(nn_file, "wb"))  
    print("test_acc_epoch:")
    print(ret_saved)
    print("avg:")
    print(avg)

In [ ]:
###------- Test stuff

In [ ]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_arc_challenge_dev_dataloader(tokenizer)

In [14]:
with  open("DL4_c_dev_arc.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("NN-ARC-Easy-Train-Race4.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [22]:
print(len(t_dataset))
print(t_dataset[3])

569
{'id': 'Mercury_7122448', 'article': [' kepler formerly known as koi is red dwarf located in the constellation cygnus and approximately light years from the sun it has three known extrasolar planets all of which are smaller than earth in radius and likely also in mass characteristics kepler mass is estimated to be times that of the sun and to have radius times that of the sun that is just times that of the gas giant jupiter due to its small radius and hence surface area the luminosity of kepler is only of that of the sun its metallicity is one third of the sun kepler has an appreciable proper motion of up to mas yr due to its small size and low temperature the star habitable zone is much closer to the star than earth is to the sun planetary system earth mars and the planets of this system compared to kepler and kepler the first terrestrial sized exoplanets to be discovered outside of the solar system the kepler system as compared to the jovian system the planetary system comprising

In [22]:
for element in t_dataset:
    if element["id"] == "TIMSS_2003_8_pg29":
        print(element["optionscore"]) 
#        element["optionscore"] = [1,2,3,4]
        print(element["answer"])
        print(element)

[]
A
{'id': 'TIMSS_2003_8_pg29', 'article': [' A non-glandular, highly vascular organ which is situated in the abdomen, on the left side, in connection with the digestive organs, and in which the blood undergoes cer- tain modifications in respect of its corpuscles.\n The pleural cavity is created by the rib cage, which surrounds and protects the lungs, and by the diaphragm, a thin, flat muscle which separates the heart and lungs from the organs of the abdomen like a sheet.\n Spinneret (n.) One of the special jointed organs situated on the under side, and near the end, of the abdomen of spiders, by means of which they spin their webs.\n The abdomen of the female is much broader than that of the male : the first and second pleopods of the male are modified into tubular or rather spout-like copulatory organs ; and the reproductive aperture is situated in the male on the XXVII REPRODUCTIVE ORGANS 343 proximal podomere of the fifth leg, in the female on that of the third.\n', " It is a musc

In [31]:
checkpoint = torch.load("/pfs/work7/workspace/scratch/st_st169719-TQA-0/Chen/Cosmos/ex02-albert-cosmos-epoch=03-val_acc_epoch=0.588.ckpt")
new_checkpoint = {}

for key in checkpoint['state_dict'].keys():
    if 'model' in key:
        new_key = key[6:]
        new_checkpoint[new_key] = checkpoint['state_dict'][key]
    else:
        new_checkpoint[key] = checkpoint['state_dict'][key]

config = AlbertConfig.from_pretrained('albert-base-v2')
m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=new_checkpoint)
m2 = AlbertModel.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=new_checkpoint)
trainer_for_test = pl.Trainer(gpus=-1, accelerator='dp')
model_for_test = TestModel(m, test_dataloader, m2)

Some weights of the model checkpoint at None were not used when initializing AlbertModel: ['classifier.weight', 'classifier.bias']
- This IS expected if you are initializing AlbertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
06/18/2021 21:58:57 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/18/2021 21:58:57 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores


In [32]:
trainer_for_test.test(model=model_for_test)

06/18/2021 21:58:59 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

!!!!!!!!!!!!!
!!!!!!!!!!!!!
!!!!!!!!!!!!!
0
!!!!!!!!!!!!!
!!!!!!!!!!!!!
!!!!!!!!!!!!!
24
[]
!!!!!!!!!!!!!
!!!!!!!!!!!!!!!!!!!!!!!!!!
!!!!!!!!!!!!!
!!!!!!!!!!!!!
16

[]
!!!!!!!!!!!!!!!!!!!!!!!!!!
!!!!!!!!!!!!!
!!!!!!!!!!!!!
20

28
[][]

!!!!!!!!!!!!!
!!!!!!!!!!!!!
!!!!!!!!!!!!!
8
[]
!!!!!!!!!!!!!
!!!!!!!!!!!!!
!!!!!!!!!!!!!
12
[]
[[ 0.8345697  -0.8700378  -0.99999887 ...  0.7896198  -1.
   0.87957287]
 [ 0.964219   -0.9659402  -0.9999613  ...  0.5427697  -1.
   0.9740845 ]
 [ 0.98322195 -0.9878952  -0.99999726 ...  0.72941655 -1.
   0.9888236 ]
 [ 0.76701653 -0.73032856 -0.99999744 ...  0.9966919  -0.9890095
   0.7957484 ]]
!!!!!!!!!!!!!
!!!!!!!!!!!!!
!!!!!!!!!!!!!
4
[[ 0.94588685 -0.95035654 -0.99999976 ...  0.51926583 -0.99999994
   0.95468646]
 [ 0.97199684 -0.97222966 -0.9999998  ...  0.84044045 -1.
   0.97474015]
 [ 0.8466149  -0.81688017 -0.9999979  ...  0.46829614 -0.92667776
   0.8562488 ]
 [ 0.98892313 -0.98633146 -0.99999434 ...  0.90680283 -1.
   0.9869539 ]]
!!!!!!!!!!!!!!!!

[{'test_acc_epoch': 0.4039497375488281, 'test_acc': 0.0}]

In [33]:
pickle.dump(t_dataset, open("AAA.pkl", "wb"))   

In [36]:
irater = iter(test_dataloader)
sample = next(irater)
print(sample)
labels = sample["label"]
input_ids = sample["input_ids"]
attention_mask = sample["attention_mask"]
token_type_ids = sample["token_type_ids"]
#outputs = m(input_ids, token_type_ids=token_type_ids, attention_mask=attention_mask, labels=labels, output_hidden_states=True)
#print(outputs.logits)
#print(outputs.logits.shape)
#print(outputs.hidden_states[-1].shape)
#print(outputs.hidden_states[-1][0:4].shape)
#print("!!!!!!!!!!!!!!!!!!!!!!!!!!!")
#print(outputs.hidden_states[-1])

{'id': ['Mercury_SC_407695', 'Mercury_7103565', 'MDSA_2009_5_16', 'Mercury_7027230', 'Mercury_SC_405487', 'Mercury_7032743', 'Mercury_7205135', 'MDSA_2007_4_52'], 'label': tensor([3, 2, 3, 0, 1, 2, 2, 2]), 'input_ids': tensor([[[    2,    14,  6289,  ...,  1170,     9,     3],
         [    2,    30,     1,  ...,     0,     0,     0],
         [    2, 12994,   108,  ...,  3001,     9,     3],
         [    2,    30,     1,  ...,  3193,     9,     3]],

        [[    2,  4958,  1961,  ...,    60,  7486,     3],
         [    2,  4958,  1961,  ...,    60,  1938,     3],
         [    2,  4958,  1961,  ...,    60, 15510,     3],
         [    2,  4958,  1961,  ...,    60, 12306,     3]],

        [[    2,    14,  2121,  ...,  1073,     9,     3],
         [    2,    14,  2121,  ...,   939,     9,     3],
         [    2,    14,  2121,  ...,  8577,     9,     3],
         [    2,    14,  2121,  ...,  8577,     9,     3]],

        ...,

        [[    2,   390,   408,  ...,     0,     0,   

In [53]:
print(sample['input_ids'].size())

torch.Size([8, 4, 512])


In [38]:
outputs_pooler = m2(input_ids = torch.reshape(sample['input_ids'],(-1,512)),
                           token_type_ids=torch.reshape(sample['token_type_ids'],(-1,512)),
                           attention_mask=torch.reshape(sample['attention_mask'],(-1,512)))

In [39]:
print(outputs_pooler.pooler_output.size())

torch.Size([32, 768])


In [49]:
test_print = outputs_pooler.pooler_output[17:21]
print(test_print.size())
print(test_print)

torch.Size([4, 768])
tensor([[ 0.9782, -0.9876, -1.0000,  ...,  0.9157, -0.2217,  0.9884],
        [ 0.9741, -0.9833, -1.0000,  ...,  0.9543,  0.9491,  0.9850],
        [ 0.9725, -0.9845, -1.0000,  ...,  0.9187, -0.5793,  0.9859],
        [ 0.4681, -0.2204, -1.0000,  ...,  0.9910,  0.9964,  0.4212]],
       grad_fn=<SliceBackward>)


In [19]:
print(len(t_dataset))
print(t_dataset[2242])

2245
{'id': 'Mercury_7010080', 'article': [' Our problem is that burning coal, oil, and gas produces carbon dioxide, which adds to the supply already in the atmosphere, increasing the greenhouse effect and thereby increasing the temperature of the Earth.\n interconnection between carbon hydrogen and oxygen cycle in metabolism of plants the carbon cycle is an essential part of life on earth about half the dry weight of most living organisms is carbon it plays an important role in the structure biochemistry and nutrition of all living cells living biomass holds about gigatons of carbon most of which is made of terrestrial plants wood while some gigatons of carbon are stored in the terrestrial biosphere as dead biomass carbon is cycled through the terrestrial biosphere with varying speeds depending on what form it is stored in and under which circumstances it is exchanged most quickly with the atmosphere although small amounts of carbon leave the terrestrial biosphere and enter the oceans

In [ ]:
###------- Test stuff end

In [20]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_arc_easy_dev_dataloader(tokenizer)

06/16/2021 23:17:58 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.094s]
06/16/2021 23:17:59 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.167s]
06/16/2021 23:17:59 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.121s]
06/16/2021 23:17:59 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.123s]
06/16/2021 23:18:00 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.882s]
06/16/2021 23:18:01 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.340s]
06/16/2021 23:18:09 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:7.571s]
06/16/2021 23:18:16 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:7.864s]
06/16/2021 23:18:30 - INFO - elasticsearch -   P

250


06/16/2021 23:32:52 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.898s]
06/16/2021 23:32:52 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.691s]
06/16/2021 23:32:53 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.633s]
06/16/2021 23:32:53 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.435s]
06/16/2021 23:32:55 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.545s]
06/16/2021 23:32:56 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.740s]
06/16/2021 23:32:57 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.812s]
06/16/2021 23:32:57 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.840s]
06/16/2021 23:32:59 - INFO - elasticsearch -   P

WASL_2005_5_11
skipped, less than 4 options


06/16/2021 23:36:47 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.568s]
06/16/2021 23:36:48 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.339s]
06/16/2021 23:36:50 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.286s]
06/16/2021 23:36:51 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.528s]
06/16/2021 23:36:52 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.690s]
06/16/2021 23:36:52 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.278s]
06/16/2021 23:36:52 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.249s]
06/16/2021 23:36:53 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.231s]
06/16/2021 23:36:53 - INFO - elasticsearch -   P

500


06/16/2021 23:41:58 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.386s]
06/16/2021 23:41:58 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.414s]
06/16/2021 23:41:59 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.329s]
06/16/2021 23:41:59 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.300s]
06/16/2021 23:42:00 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.746s]
06/16/2021 23:42:01 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.969s]
06/16/2021 23:42:01 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.708s]
06/16/2021 23:42:02 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.025s]
06/16/2021 23:42:03 - INFO - elasticsearch -   P

Saving data to cache4_e_dev_arc.cache...


In [ ]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_arc_challenge_dev_dataloader(tokenizer)

06/16/2021 23:45:31 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.315s]
06/16/2021 23:45:33 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.301s]
06/16/2021 23:45:34 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.342s]
06/16/2021 23:45:36 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.551s]
06/16/2021 23:45:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.399s]
06/16/2021 23:45:40 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.961s]
06/16/2021 23:45:42 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.941s]
06/16/2021 23:45:44 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.931s]
06/16/2021 23:45:47 - INFO - elasticsearch -   P

NYSEDREGENTS_2014_4_4
skipped, less than 4 options


06/16/2021 23:48:09 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.300s]
06/16/2021 23:48:09 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.369s]
06/16/2021 23:48:09 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.242s]
06/16/2021 23:48:10 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.298s]
06/16/2021 23:48:12 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.853s]
06/16/2021 23:48:15 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.410s]
06/16/2021 23:48:18 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.662s]
06/16/2021 23:48:20 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.480s]
06/16/2021 23:48:21 - INFO - elasticsearch -   P

NYSEDREGENTS_2014_4_19
skipped, less than 4 options


06/16/2021 23:49:17 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.431s]
06/16/2021 23:49:18 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.460s]
06/16/2021 23:49:18 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.533s]
06/16/2021 23:49:19 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.506s]
06/16/2021 23:49:19 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.238s]
06/16/2021 23:49:19 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.244s]
06/16/2021 23:49:20 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.260s]
06/16/2021 23:49:20 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.260s]
06/16/2021 23:49:21 - INFO - elasticsearch -   P

...

NYSEDREGENTS_2014_4_28
skipped, less than 4 options


06/16/2021 23:56:27 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.118s]
06/16/2021 23:56:28 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.832s]
06/16/2021 23:56:28 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.907s]
06/16/2021 23:56:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.065s]
06/16/2021 23:56:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.093s]
06/16/2021 23:56:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.076s]
06/16/2021 23:56:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.065s]
06/16/2021 23:56:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.120s]
06/16/2021 23:56:30 - INFO - elasticsearch -   P

250


06/16/2021 23:56:40 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.353s]
06/16/2021 23:56:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.343s]
06/16/2021 23:56:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.282s]
06/16/2021 23:56:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.246s]
06/16/2021 23:56:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.164s]
06/16/2021 23:56:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.150s]
06/16/2021 23:56:42 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.236s]
06/16/2021 23:56:42 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.157s]
06/16/2021 23:56:43 - INFO - elasticsearch -   P

Saving data to cache4_c_dev_arc.cache...


In [23]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_arc_challenge_train_dataloader(tokenizer)

06/17/2021 00:04:28 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.117s]
06/17/2021 00:04:29 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.469s]
06/17/2021 00:04:29 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.616s]
06/17/2021 00:04:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.547s]
06/17/2021 00:04:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.237s]
06/17/2021 00:04:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.112s]
06/17/2021 00:04:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.116s]
06/17/2021 00:04:31 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.145s]
06/17/2021 00:04:31 - INFO - elasticsearch -   P

250


06/17/2021 00:13:11 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.364s]
06/17/2021 00:13:11 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.347s]
06/17/2021 00:13:12 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.372s]
06/17/2021 00:13:12 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.455s]
06/17/2021 00:13:12 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.320s]
06/17/2021 00:13:13 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.241s]
06/17/2021 00:13:13 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.351s]
06/17/2021 00:13:13 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.269s]
06/17/2021 00:13:14 - INFO - elasticsearch -   P

NYSEDREGENTS_2004_4_8
skipped, less than 4 options


06/17/2021 00:24:34 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.734s]
06/17/2021 00:24:35 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.717s]
06/17/2021 00:24:36 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.754s]
06/17/2021 00:24:37 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.731s]
06/17/2021 00:24:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.601s]
06/17/2021 00:24:39 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.825s]
06/17/2021 00:24:40 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.523s]
06/17/2021 00:24:40 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.534s]
06/17/2021 00:24:43 - INFO - elasticsearch -   P

...

750


06/17/2021 00:38:19 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.368s]
06/17/2021 00:38:19 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.768s]
06/17/2021 00:38:20 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.898s]
06/17/2021 00:38:21 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.740s]
06/17/2021 00:38:22 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.194s]
06/17/2021 00:38:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.533s]
06/17/2021 00:38:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.606s]
06/17/2021 00:38:24 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.574s]
06/17/2021 00:38:28 - INFO - elasticsearch -   P

1000


06/17/2021 00:51:05 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.436s]
06/17/2021 00:51:06 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.173s]
06/17/2021 00:51:07 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.159s]
06/17/2021 00:51:08 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.016s]
06/17/2021 00:51:08 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.395s]
06/17/2021 00:51:09 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.656s]
06/17/2021 00:51:10 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.492s]
06/17/2021 00:51:10 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.640s]
06/17/2021 00:51:12 - INFO - elasticsearch -   P

Saving data to cache4_c_train_arc.cache...


In [13]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_arc_easy_train_dataloader(tokenizer)

loading
ds_backup_0.pkl
loading
ds_backup_1.pkl
loading
ds_backup_2.pkl
loading
ds_backup_3.pkl


06/17/2021 08:59:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:20.298s]
06/17/2021 08:59:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:6.821s]
06/17/2021 08:59:36 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:6.134s]
06/17/2021 08:59:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:4.848s]
06/17/2021 08:59:58 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:16.780s]
06/17/2021 09:00:01 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:3.241s]
06/17/2021 09:00:02 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.642s]
06/17/2021 09:00:04 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.543s]
06/17/2021 09:00:19 - INFO - elasticsearch -  

NYSEDREGENTS_2009_4_12
skipped, less than 4 options


06/17/2021 09:04:34 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.742s]
06/17/2021 09:04:35 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.945s]
06/17/2021 09:04:36 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.014s]
06/17/2021 09:04:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.108s]
06/17/2021 09:04:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.281s]
06/17/2021 09:04:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.266s]
06/17/2021 09:04:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.266s]
06/17/2021 09:04:39 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.427s]
06/17/2021 09:04:42 - INFO - elasticsearch -   P

250


06/17/2021 09:10:45 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.211s]
06/17/2021 09:10:45 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.085s]
06/17/2021 09:10:45 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.046s]
06/17/2021 09:10:45 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.090s]
06/17/2021 09:10:46 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.649s]
06/17/2021 09:10:46 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.500s]
06/17/2021 09:10:47 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.767s]
06/17/2021 09:10:48 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.440s]
06/17/2021 09:10:48 - INFO - elasticsearch -   P

Saving data to cache4_e_train_arc.cache...


In [30]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_ob_dev_dataloader(tokenizer)

06/15/2021 21:03:10 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.457s]
06/15/2021 21:03:11 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.294s]
06/15/2021 21:03:11 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.378s]
06/15/2021 21:03:11 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.415s]
06/15/2021 21:03:12 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.169s]
06/15/2021 21:03:12 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.144s]
06/15/2021 21:03:12 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.186s]
06/15/2021 21:03:12 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.196s]
06/15/2021 21:03:13 - INFO - elasticsearch -   P

250


06/15/2021 21:07:47 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.356s]
06/15/2021 21:07:47 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.397s]
06/15/2021 21:07:48 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.449s]
06/15/2021 21:07:48 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.335s]
06/15/2021 21:07:48 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.090s]
06/15/2021 21:07:48 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.043s]
06/15/2021 21:07:48 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.052s]
06/15/2021 21:07:48 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.053s]
06/15/2021 21:07:48 - INFO - elasticsearch -   P

500


Truncation was not explicitly activated but `max_length` is provided a specific value, please use `truncation=True` to explicitly truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.


Saving data to cache4_dev_ob.cache...


In [41]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_ob_test_dataloader(tokenizer)

06/16/2021 09:29:59 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.034s]
06/16/2021 09:30:01 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.019s]
06/16/2021 09:30:03 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.722s]
06/16/2021 09:30:05 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.178s]
06/16/2021 09:30:05 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.234s]
06/16/2021 09:30:06 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.218s]
06/16/2021 09:30:06 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.225s]
06/16/2021 09:30:06 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.235s]
06/16/2021 09:30:06 - INFO - elasticsearch -   P

Saving data to cache4_test_ob.cache...


In [47]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_ob_train_dataloader(tokenizer)

06/15/2021 22:26:29 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.080s]
06/15/2021 22:26:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.300s]
06/15/2021 22:26:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.059s]
06/15/2021 22:26:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.044s]
06/15/2021 22:26:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.157s]
06/15/2021 22:26:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.095s]
06/15/2021 22:26:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.348s]
06/15/2021 22:26:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.179s]
06/15/2021 22:26:31 - INFO - elasticsearch -   P

250


06/15/2021 22:30:22 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.166s]
06/15/2021 22:30:22 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.203s]
06/15/2021 22:30:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.204s]
06/15/2021 22:30:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.063s]
06/15/2021 22:30:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.021s]
06/15/2021 22:30:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.061s]
06/15/2021 22:30:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.068s]
06/15/2021 22:30:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.288s]
06/15/2021 22:30:23 - INFO - elasticsearch -   P

500


06/15/2021 22:34:18 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.425s]
06/15/2021 22:34:18 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.346s]
06/15/2021 22:34:19 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.442s]
06/15/2021 22:34:19 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.434s]
06/15/2021 22:34:19 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.078s]
06/15/2021 22:34:20 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.080s]
06/15/2021 22:34:20 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.090s]
06/15/2021 22:34:20 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.145s]
06/15/2021 22:34:20 - INFO - elasticsearch -   P

...

4500


06/15/2021 23:47:15 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.063s]
06/15/2021 23:47:15 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.122s]
06/15/2021 23:47:15 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.086s]
06/15/2021 23:47:15 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.113s]
06/15/2021 23:47:16 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.116s]
06/15/2021 23:47:16 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.074s]
06/15/2021 23:47:16 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.108s]
06/15/2021 23:47:16 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.096s]
06/15/2021 23:47:16 - INFO - elasticsearch -   P

4750


06/15/2021 23:50:50 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.624s]
06/15/2021 23:50:50 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.553s]
06/15/2021 23:50:51 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.624s]
06/15/2021 23:50:51 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.478s]
06/15/2021 23:50:52 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.415s]
06/15/2021 23:50:52 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.452s]
06/15/2021 23:50:53 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.501s]
06/15/2021 23:50:53 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.435s]
06/15/2021 23:50:53 - INFO - elasticsearch -   P

Saving data to cache4_train_ob.cache...


In [31]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_commonqa_dev_dataloader(tokenizer)

06/15/2021 21:12:20 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.840s]
06/15/2021 21:12:21 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.683s]
06/15/2021 21:12:22 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.760s]
06/15/2021 21:12:22 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.610s]
06/15/2021 21:12:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.272s]
06/15/2021 21:12:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.376s]
06/15/2021 21:12:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.215s]
06/15/2021 21:12:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.167s]
06/15/2021 21:12:24 - INFO - elasticsearch -   P

57f92025d860e32c4e780c0d51c1c20c
Too many :
1


06/15/2021 21:12:33 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.172s]
06/15/2021 21:12:33 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.176s]
06/15/2021 21:12:33 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.134s]
06/15/2021 21:12:33 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.497s]
06/15/2021 21:12:34 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.400s]
06/15/2021 21:12:34 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.468s]
06/15/2021 21:12:35 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.413s]
06/15/2021 21:12:35 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.109s]
06/15/2021 21:12:35 - INFO - elasticsearch -   P

6dc5b2884737e66543ce65f8dc40c992
Too many :
1


06/15/2021 21:12:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.219s]
06/15/2021 21:12:39 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.150s]
06/15/2021 21:12:39 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.175s]


...

01794dde3ca2991615f1aa2f63fb22e3
Too many :
2


06/15/2021 21:42:35 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.089s]
06/15/2021 21:42:36 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.987s]
06/15/2021 21:42:37 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.967s]
06/15/2021 21:42:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.111s]
06/15/2021 21:42:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.199s]
06/15/2021 21:42:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.115s]
06/15/2021 21:42:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.107s]
06/15/2021 21:42:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.132s]


ace8fa2943ba8414aebdb74b48906fae
Too many :
1


06/15/2021 21:42:39 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.336s]
06/15/2021 21:42:39 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.326s]
06/15/2021 21:42:39 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.247s]
06/15/2021 21:42:39 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.231s]
06/15/2021 21:42:40 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.247s]
06/15/2021 21:42:40 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.287s]
06/15/2021 21:42:40 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.289s]
06/15/2021 21:42:40 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.250s]
06/15/2021 21:42:41 - INFO - elasticsearch -   P

Saving data to cache4_dev_commonqa.cache...


In [ ]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_commonqa_test_dataloader(tokenizer)

In [17]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_commonqa_train_dataloader(tokenizer)

loading
ds_backup_0.pkl
loading
ds_backup_1.pkl
loading
ds_backup_2.pkl
loading
ds_backup_3.pkl
loading
ds_backup_4.pkl
loading
ds_backup_5.pkl
loading
ds_backup_6.pkl
loading
ds_backup_7.pkl
loading
ds_backup_8.pkl
loading
ds_backup_9.pkl
loading
ds_backup_10.pkl
loading
ds_backup_11.pkl
loading
ds_backup_12.pkl
loading
ds_backup_13.pkl
loading
ds_backup_14.pkl
loading
ds_backup_15.pkl
loading
ds_backup_16.pkl
loading
ds_backup_17.pkl


06/16/2021 14:48:02 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:25.562s]
06/16/2021 14:48:03 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.095s]
06/16/2021 14:48:05 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.520s]
06/16/2021 14:48:06 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.267s]
06/16/2021 14:48:34 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:28.156s]
06/16/2021 14:48:36 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.210s]
06/16/2021 14:48:37 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.334s]
06/16/2021 14:48:39 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.521s]


e4fbaf55465b6e390fa19ac32f5de707
Too many :
1


06/16/2021 14:48:46 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:6.246s]
06/16/2021 14:48:47 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.903s]
06/16/2021 14:48:48 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.909s]
06/16/2021 14:48:49 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.260s]


8a6641b5e08792fc30dcd6e1b4b97fe5
Too many :
1


...

03587acf08013444ce90fb2096bd9de8
Too many :
2


06/16/2021 15:11:01 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.596s]
06/16/2021 15:11:02 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.885s]
06/16/2021 15:11:03 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.575s]
06/16/2021 15:11:03 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.518s]
06/16/2021 15:11:04 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.649s]
06/16/2021 15:11:04 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.411s]
06/16/2021 15:11:05 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.532s]
06/16/2021 15:11:05 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.421s]
06/16/2021 15:11:06 - INFO - elasticsearch -   P

f1b2a30a1facff543e055231c5f90dd0
Too many :
2


06/16/2021 15:11:08 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.534s]
06/16/2021 15:11:09 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.637s]
06/16/2021 15:11:10 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.681s]
06/16/2021 15:11:10 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.667s]
06/16/2021 15:11:11 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.228s]
06/16/2021 15:11:11 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.218s]
06/16/2021 15:11:11 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.210s]
06/16/2021 15:11:11 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.225s]
06/16/2021 15:11:12 - INFO - elasticsearch -   P

Saving data to cache4_train_commonqa.cache...


In [67]:
with  open("DL"+iter_version+"_e_dev_arc.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("DS"+iter_version+"_e_dev_arc.pkl", 'rb') as f:
    t_dataset = pickle.load(f)
    
NN_filename = "NN-ARC-Easy-Dev-OB"+iter_version+".pkl"
model_path = "/pfs/work7/workspace/scratch/st_st169719-TQA-0/Chen/OpenBook/dr_ex01-albert-openbook-epoch=02-val_acc_epoch=0.557.ckpt"

In [68]:
Generate_NN_file(model_path, NN_filename, 20)

Some weights of the model checkpoint at None were not used when initializing AlbertModel: ['classifier.weight', 'classifier.bias']
- This IS expected if you are initializing AlbertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
06/18/2021 22:33:02 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/18/2021 22:33:02 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/18/2021 22:33:02 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/18/2021 22:33:17 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.27692997455596924}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/18/2021 22:37:48 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.3375224471092224}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.2957809567451477}
--------------------------------------------------------------------------------
test_acc_epoch:
0.3375224471092224
avg:
0.27542638704180716


In [69]:
with  open("DL"+iter_version+"_e_dev_arc.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("DS"+iter_version+"_e_dev_arc.pkl", 'rb') as f:
    t_dataset = pickle.load(f)
    
NN_filename = "NN-ARC-Easy-Dev-Commonqa"+iter_version+".pkl"
model_path = "/pfs/work7/workspace/scratch/st_st169719-TQA-0/Chen/Commonsense/dr_ex01-albert-commonsense-epoch=01-val_loss_epoch=1.066.ckpt"

In [ ]:
Generate_NN_file(model_path, NN_filename, 20)

Some weights of the model checkpoint at None were not used when initializing AlbertModel: ['classifier.weight', 'classifier.bias']
- This IS expected if you are initializing AlbertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
06/18/2021 22:38:05 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/18/2021 22:38:05 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/18/2021 22:38:05 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

In [76]:
with  open("DL"+iter_version+"_e_dev_arc.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("DS"+iter_version+"_e_dev_arc.pkl", 'rb') as f:
    t_dataset = pickle.load(f)
    
NN_filename = "NN-ARC-Easy-Dev-Race"+iter_version+".pkl"
model_path = "/pfs/work7/workspace/scratch/st_st169719-TQA-0/Chen/RACE/e3-albert-race-epoch=01-val_loss_epoch=1.16.ckpt"

In [77]:
Generate_NN_file(model_path, NN_filename, 20)

Some weights of the model checkpoint at None were not used when initializing AlbertModel: ['classifier.weight', 'classifier.bias']
- This IS expected if you are initializing AlbertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
06/18/2021 22:44:30 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/18/2021 22:44:30 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/18/2021 22:44:30 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/18/2021 22:44:45 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.5282765030860901}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/18/2021 22:49:16 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.5848294496536255}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.5525134801864624}
--------------------------------------------------------------------------------
test_acc_epoch:
0.5848294496536255
avg:
0.5398114860057831


In [78]:
with  open("DL"+iter_version+"_e_dev_arc.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("DS"+iter_version+"_e_dev_arc.pkl", 'rb') as f:
    t_dataset = pickle.load(f)
    
NN_filename = "NN-ARC-Easy-Dev-CQA"+iter_version+".pkl"
model_path = "/pfs/work7/workspace/scratch/st_st169719-TQA-0/Chen/Cosmos/ex02-albert-cosmos-epoch=03-val_acc_epoch=0.588.ckpt"

In [79]:
Generate_NN_file(model_path, NN_filename, 20)

Some weights of the model checkpoint at None were not used when initializing AlbertModel: ['classifier.weight', 'classifier.bias']
- This IS expected if you are initializing AlbertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
06/18/2021 22:49:32 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/18/2021 22:49:32 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/18/2021 22:49:32 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/18/2021 22:49:47 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.3671454191207886}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/18/2021 22:54:18 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.3626570999622345}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.41382405161857605}
--------------------------------------------------------------------------------
test_acc_epoch:
0.43177738785743713
avg:
0.38649012595415116


In [82]:
with  open("DL"+iter_version+"_e_train_arc.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("DS"+iter_version+"_e_train_arc.pkl", 'rb') as f:
    t_dataset = pickle.load(f)
    
NN_filename = "NN-ARC-Easy-Train-OB"+iter_version+".pkl"
model_path = "/pfs/work7/workspace/scratch/st_st169719-TQA-0/Chen/OpenBook/dr_ex01-albert-openbook-epoch=02-val_acc_epoch=0.557.ckpt"

In [83]:
Generate_NN_file(model_path, NN_filename, 10)

Some weights of the model checkpoint at None were not used when initializing AlbertModel: ['classifier.weight', 'classifier.bias']
- This IS expected if you are initializing AlbertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
06/18/2021 22:55:00 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/18/2021 22:55:00 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/18/2021 22:55:00 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/18/2021 22:56:04 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.26875415444374084}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/18/2021 23:04:18 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.24684664607048035}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.2496127486228943}
--------------------------------------------------------------------------------
test_acc_epoch:
0.2751714885234833
avg:
0.2557977423071861


In [84]:
with  open("DL"+iter_version+"_e_train_arc.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("DS"+iter_version+"_e_train_arc.pkl", 'rb') as f:
    t_dataset = pickle.load(f)
    
NN_filename = "NN-ARC-Easy-Train-Commonqa"+iter_version+".pkl"
model_path = "/pfs/work7/workspace/scratch/st_st169719-TQA-0/Chen/Commonsense/dr_ex01-albert-commonsense-epoch=01-val_loss_epoch=1.066.ckpt"

In [85]:
Generate_NN_file(model_path, NN_filename, 10)

Some weights of the model checkpoint at None were not used when initializing AlbertModel: ['classifier.weight', 'classifier.bias']
- This IS expected if you are initializing AlbertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
06/18/2021 23:05:25 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/18/2021 23:05:25 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/18/2021 23:05:25 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/18/2021 23:06:26 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.5095154047012329}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/18/2021 23:14:38 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.511506974697113}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.4424651563167572}
--------------------------------------------------------------------------------
test_acc_epoch:
0.51338791847229
avg:
0.4941248118877411


In [86]:
with  open("DL"+iter_version+"_e_train_arc.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("DS"+iter_version+"_e_train_arc.pkl", 'rb') as f:
    t_dataset = pickle.load(f)
    
NN_filename = "NN-ARC-Easy-Train-Race"+iter_version+".pkl"
model_path = "/pfs/work7/workspace/scratch/st_st169719-TQA-0/Chen/RACE/e3-albert-race-epoch=01-val_loss_epoch=1.16.ckpt"

In [87]:
Generate_NN_file(model_path, NN_filename, 10)

Some weights of the model checkpoint at None were not used when initializing AlbertModel: ['classifier.weight', 'classifier.bias']
- This IS expected if you are initializing AlbertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
06/18/2021 23:15:42 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/18/2021 23:15:42 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/18/2021 23:15:42 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/18/2021 23:16:43 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.5352954268455505}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/18/2021 23:24:56 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.4917016923427582}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.5200265645980835}
--------------------------------------------------------------------------------
test_acc_epoch:
0.5674927830696106
avg:
0.5245408266782761


In [88]:
with  open("DL"+iter_version+"_e_train_arc.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("DS"+iter_version+"_e_train_arc.pkl", 'rb') as f:
    t_dataset = pickle.load(f)
    
NN_filename = "NN-ARC-Easy-Train-CQA"+iter_version+".pkl"
model_path = "/pfs/work7/workspace/scratch/st_st169719-TQA-0/Chen/Cosmos/ex02-albert-cosmos-epoch=03-val_acc_epoch=0.588.ckpt"

In [89]:
Generate_NN_file(model_path, NN_filename, 10)

Some weights of the model checkpoint at None were not used when initializing AlbertModel: ['classifier.weight', 'classifier.bias']
- This IS expected if you are initializing AlbertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
06/18/2021 23:25:59 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/18/2021 23:25:59 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/18/2021 23:25:59 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/18/2021 23:27:01 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 1.0, 'test_acc_epoch': 0.4482186436653137}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/18/2021 23:35:13 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 1.0, 'test_acc_epoch': 0.4447886645793915}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 1.0, 'test_acc_epoch': 0.44412481784820557}
--------------------------------------------------------------------------------
test_acc_epoch:
0.4482186436653137
avg:
0.4266098767518997


In [90]:
with  open("DL"+iter_version+"_c_dev_arc.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("DS"+iter_version+"_c_dev_arc.pkl", 'rb') as f:
    t_dataset = pickle.load(f)
    
NN_filename = "NN-ARC-Challenge-Dev-OB"+iter_version+".pkl"
model_path = "/pfs/work7/workspace/scratch/st_st169719-TQA-0/Chen/OpenBook/dr_ex01-albert-openbook-epoch=02-val_acc_epoch=0.557.ckpt"

In [91]:
Generate_NN_file(model_path, NN_filename, 10)

Some weights of the model checkpoint at None were not used when initializing AlbertModel: ['classifier.weight', 'classifier.bias']
- This IS expected if you are initializing AlbertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
06/18/2021 23:36:15 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/18/2021 23:36:15 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/18/2021 23:36:15 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/18/2021 23:36:23 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.4285714328289032}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/18/2021 23:37:26 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.4285714328289032}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.4158163368701935}
--------------------------------------------------------------------------------
test_acc_epoch:
0.4285714328289032
avg:
0.4148809552192688


In [92]:
with  open("DL"+iter_version+"_c_dev_arc.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("DS"+iter_version+"_c_dev_arc.pkl", 'rb') as f:
    t_dataset = pickle.load(f)
    
NN_filename = "NN-ARC-Challenge-Dev-Commonqa"+iter_version+".pkl"
model_path = "/pfs/work7/workspace/scratch/st_st169719-TQA-0/Chen/Commonsense/dr_ex01-albert-commonsense-epoch=01-val_loss_epoch=1.066.ckpt"

In [93]:
Generate_NN_file(model_path, NN_filename, 10)

Some weights of the model checkpoint at None were not used when initializing AlbertModel: ['classifier.weight', 'classifier.bias']
- This IS expected if you are initializing AlbertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
06/18/2021 23:37:35 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/18/2021 23:37:35 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/18/2021 23:37:35 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/18/2021 23:37:42 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.30102041363716125}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/18/2021 23:38:45 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.30102041363716125}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.30102041363716125}
--------------------------------------------------------------------------------
test_acc_epoch:
0.3265306055545807
avg:
0.3062925159931183


In [94]:
with  open("DL"+iter_version+"_c_dev_arc.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("DS"+iter_version+"_c_dev_arc.pkl", 'rb') as f:
    t_dataset = pickle.load(f)
    
NN_filename = "NN-ARC-Challenge-Dev-Race"+iter_version+".pkl"
model_path = "/pfs/work7/workspace/scratch/st_st169719-TQA-0/Chen/RACE/e3-albert-race-epoch=01-val_loss_epoch=1.16.ckpt"

In [95]:
Generate_NN_file(model_path, NN_filename, 10)

Some weights of the model checkpoint at None were not used when initializing AlbertModel: ['classifier.weight', 'classifier.bias']
- This IS expected if you are initializing AlbertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
06/18/2021 23:38:53 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/18/2021 23:38:53 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/18/2021 23:38:53 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/18/2021 23:39:01 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.3979591727256775}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/18/2021 23:40:04 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.386904776096344}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.37244898080825806}
--------------------------------------------------------------------------------
test_acc_epoch:
0.40136054158210754
avg:
0.37984693944454195


In [96]:
with  open("DL"+iter_version+"_c_dev_arc.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("DS"+iter_version+"_c_dev_arc.pkl", 'rb') as f:
    t_dataset = pickle.load(f)
    
NN_filename = "NN-ARC-Challenge-Dev-CQA"+iter_version+".pkl"
model_path = "/pfs/work7/workspace/scratch/st_st169719-TQA-0/Chen/Cosmos/ex02-albert-cosmos-epoch=03-val_acc_epoch=0.588.ckpt"

In [97]:
Generate_NN_file(model_path, NN_filename, 10)

Some weights of the model checkpoint at None were not used when initializing AlbertModel: ['classifier.weight', 'classifier.bias']
- This IS expected if you are initializing AlbertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
06/18/2021 23:40:12 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/18/2021 23:40:12 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/18/2021 23:40:12 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/18/2021 23:40:20 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.3095238208770752}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/18/2021 23:41:23 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.3044217824935913}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.3044217824935913}
--------------------------------------------------------------------------------
test_acc_epoch:
0.3095238208770752
avg:
0.2934523820877075


In [98]:
with  open("DL"+iter_version+"_c_train_arc.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("DS"+iter_version+"_c_train_arc.pkl", 'rb') as f:
    t_dataset = pickle.load(f)
    
NN_filename = "NN-ARC-Challenge-Train-OB"+iter_version+".pkl"
model_path = "/pfs/work7/workspace/scratch/st_st169719-TQA-0/Chen/OpenBook/dr_ex01-albert-openbook-epoch=02-val_acc_epoch=0.557.ckpt"

In [99]:
Generate_NN_file(model_path, NN_filename, 10)

Some weights of the model checkpoint at None were not used when initializing AlbertModel: ['classifier.weight', 'classifier.bias']
- This IS expected if you are initializing AlbertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
06/18/2021 23:41:32 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/18/2021 23:41:32 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/18/2021 23:41:32 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/18/2021 23:42:02 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.3015981614589691}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/18/2021 23:46:00 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.32488584518432617}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.30388128757476807}
--------------------------------------------------------------------------------
test_acc_epoch:
0.358219176530838
avg:
0.32036529779434203


In [100]:
with  open("DL"+iter_version+"_c_train_arc.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("DS"+iter_version+"_c_train_arc.pkl", 'rb') as f:
    t_dataset = pickle.load(f)
    
NN_filename = "NN-ARC-Challenge-Train-Commonqa"+iter_version+".pkl"
model_path = "/pfs/work7/workspace/scratch/st_st169719-TQA-0/Chen/Commonsense/dr_ex01-albert-commonsense-epoch=01-val_loss_epoch=1.066.ckpt"

In [101]:
Generate_NN_file(model_path, NN_filename, 10)

Some weights of the model checkpoint at None were not used when initializing AlbertModel: ['classifier.weight', 'classifier.bias']
- This IS expected if you are initializing AlbertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
06/18/2021 23:46:31 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/18/2021 23:46:31 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/18/2021 23:46:31 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/18/2021 23:47:01 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.27328768372535706}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/18/2021 23:51:00 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.2705479562282562}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.2710045576095581}
--------------------------------------------------------------------------------
test_acc_epoch:
0.28538814187049866
avg:
0.25805936455726625


In [102]:
with  open("DL"+iter_version+"_c_train_arc.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("DS"+iter_version+"_c_train_arc.pkl", 'rb') as f:
    t_dataset = pickle.load(f)
    
NN_filename = "Challenge-Train-Race"+iter_version+".pkl"
model_path = "/pfs/work7/workspace/scratch/st_st169719-TQA-0/Chen/RACE/e3-albert-race-epoch=01-val_loss_epoch=1.16.ckpt"

In [103]:
Generate_NN_file(model_path, NN_filename, 10)

Some weights of the model checkpoint at None were not used when initializing AlbertModel: ['classifier.weight', 'classifier.bias']
- This IS expected if you are initializing AlbertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
06/18/2021 23:51:31 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/18/2021 23:51:31 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/18/2021 23:51:31 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/18/2021 23:52:01 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.35205480456352234}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/18/2021 23:55:59 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.3086757957935333}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.31598174571990967}
--------------------------------------------------------------------------------
test_acc_epoch:
0.3643835484981537
avg:
0.33125571310520174


In [104]:
with  open("DL"+iter_version+"_c_train_arc.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("DS"+iter_version+"_c_train_arc.pkl", 'rb') as f:
    t_dataset = pickle.load(f)
    
NN_filename = "NN-ARC-Challenge-Train-CQA"+iter_version+".pkl"
model_path = "/pfs/work7/workspace/scratch/st_st169719-TQA-0/Chen/Cosmos/ex02-albert-cosmos-epoch=03-val_acc_epoch=0.588.ckpt"

In [105]:
Generate_NN_file(model_path, NN_filename, 10)

Some weights of the model checkpoint at None were not used when initializing AlbertModel: ['classifier.weight', 'classifier.bias']
- This IS expected if you are initializing AlbertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
06/18/2021 23:56:31 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/18/2021 23:56:31 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/18/2021 23:56:31 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/18/2021 23:57:01 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.3027397394180298}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/19/2021 00:00:59 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.2997716963291168}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.33036530017852783}
--------------------------------------------------------------------------------
test_acc_epoch:
0.33036530017852783
avg:
0.29045661985874177
